In [9]:
from modelEq import saturation, alloAct, alloInhib
from util import printBlockMessage
from units import cnt2mol
import plotly.express as px
import plotly.graph_objects as go
import numpy as np
from random import randint
from scipy.constants import Avogadro
from plotly.subplots import make_subplots
from dataclasses import dataclass

DICT_TIME = {
    'simDurationSeconds':5000, #172800, #48 hrs if 1s
    'simStepsPerSecond': 1,
    }
# Format: moleculename: (concentration uM, type) 
# Type can be 'met' for metabolite or 'enz' for enzyme
DICT_T0_CONC = {
            # Changeable met concs
            'Gluc' : (5000, 'met'),
            'F6P' :  (0, 'met'),          # Goal: 8.8mM - https://www.nature.com/articles/nchembio.186.pdf,
            'F16BP' :(0, 'met'),        # Goal: 15.0mM - https://www.nature.com/articles/nchembio.186.pdf
            'PEP' :  (0, 'met'),         # Goal: 0.18mM - https://www.nature.com/articles/nchembio.186.pdf
            'ADP' :  (560, 'met'),           # Goal: 0.56mM - https://www.nature.com/articles/nchembio.186.pdf
            'ATP' :  (9600, 'met'),
            'PYR' :  (0, 'met'),
            # Changeable enz concs
            'PFKa' : (1e-3, 'enz'),
            'PFKi' : (1e-3, 'enz'),
            'PFKb' : (5e-3, 'enz'),
            # Unchanging Enzyme Concs:
            'HK' :   (7e-3, 'enz'),
            'PEPWELD' : (4.5e-3, 'enz'),
            'PK' :   (7.0e-2, 'enz'),
        }
DICT_KCAT = {
    'PFKa':1e2,
    'PFKi':1e2,
    'HK' : 4e3,
    'PK' : 1.7e3,
    'PEPWELD' : 1e3
    }
DICT_K = {
    'PFKa-->PFKb':1e-3,
    'PFKi-->PFKb':1e-3,
    'PFKa-->PFKi':cnt2mol(5e11, 'micro'),
    'PFKi-->PFKa':cnt2mol(5e11, 'micro'),
    }
DICT_KM = {
    'PFKb_PFKb':5e-7,
    'PFKb_PFKa':1e-2,
    'PFKb_PFKi':1e-2,
    'PFKb_ADP': 550.0,
    'PFKb_PEP': 5e-2,
    'PFKa_F6P': 1.0,
    'PFKa_ATP': 60,
    'PFKi_F6P': 1e7,
    'PFKi_ATP': 60,
    'HK_Gluc' : 500.0,
    'HK_ATP' : 15000.0,
    'PEPWELD_F16BP' : 5000.0,
    'PK_PEP' : 35.0,
    'PK_ADP' : 50.0,
    }
DICT_K_REGULATORY = {
    # Format: Ka/Ki_Molecule_Target
    # Ki
    'Ki_PYR_HK' : 50.0,
    'Ki_PEP_PFK' : 100.0,
    'Ki_ATP_PK' : 12000.0,
    'Ki_PEP_PEPWELD' : 400.0,
    'Ki_F6P_HK' : 20.0,
    # Ka
    'Ka_F16BP_PK' : 100.0
}

DICT_ENZ_SUBSTRATE = {
    'HK' : {'subs':[('Gluc','sat'), ('ATP','sat')], 'prod':[('F6P','sat'), ('ADP','sat')], 'alloI':[('F6P','AlloI')],},
    'PFKa' :  {'subs':[('F6P','sat'), ('ATP','sat')], 'prod':[('F16BP','sat'), ('ADP','sat')]},
    'PFKi' :{'subs':[('F6P','sat'), ('ATP','sat')], 'prod':[('F16BP','sat'), ('ADP','sat')]},
    'PFKb' : {'subs':[('ADP','sat'), ('PEP','sat')], 'prod':[('PFKa','sat'), ('PFKi','sat')]},
    'PEPWELD' : {'subs':[('F16BP','sat')], 'prod':[('PEP','sat')]},
    'PK' : {'subs':[('PEP','sat'), ('ADP','sat')], 'prod':[('PYR','sat'), ('ATP','sat')], 'alloI':[('ATP', 'AlloI')], 'alloA':[('F16BP', 'AlloA')]},    
}

In [11]:
CELL_CYCLE_ATP_DEMAND = cnt2mol(1080, 'micro')
CELL_CYCLE_ATP_DEMAND

1.7933821925477544e-15

In [13]:
@dataclass 
class KValue:
    ktype:str = ""
    ktarget:str = ""
    kval:float = 0.0
    
mol = {
        # Changeable met concs
        'Gluc' : {'val':5000.0, 'unit':'uM','moltype':'met', 'kval':[
            KValue("sat", "HK", 500.0)
        ]},
        'F6P' : {'val':0.0, 'unit':'uM','moltype':'met', 'kval':[
            KValue("sat", "PFKa", 1.0),
            KValue("sat", "PFKi", 1e7),
            KValue("alloI", "HK", 20.0),
        ]},
        'F16BP' : {'val':0.0, 'unit':'uM','moltype':'met', 'kval':[
            KValue("sat", "PEPWELD", 5000.0),
            KValue("alloA", "PK", 400.0)
        ]},
        'PEP' : {'val':0.0, 'unit':'uM','moltype':'met', 'kval':[
            KValue("sat", "PK", 35.0),
            KValue("sat", "PFKb", 5e-2),
        ]},
        'ADP' : {'val':560.0, 'unit':'uM','moltype':'met', 'kval':[
            KValue("sat", "PK", 50.0),
            KValue("sat", "PFKb", 550.0),
        ]},
        'ATP' : {'val':9600.0, 'unit':'uM','moltype':'met', 'kval':[
            KValue("sat", "PFKa", 60.0),
            KValue("sat", "PFKi", 60.0),
            KValue("sat", "HK", 15000.0),
            KValue("alloI", "PK", 12000.0),
        ]},
        'PYR' : {'val':0.0, 'unit':'uM','moltype':'met', 'kval':[]},
        # Changeable enz concs
        'PFKa' : {'val':1e-3, 'unit':'uM','moltype':'enz', 'kval':[
            # Note this will change b/c some enzymes can catalyze more than 1 reaction with different kvals
            KValue("kcat", "", 1e2)
        ]},
        'PFKi' : {'val':1e-3, 'unit':'uM','moltype':'enz', 'kval':[
            KValue("kcat", "", 1e2)
        ]},
        'PFKb' : {'val':5e-3, 'unit':'uM','moltype':'enz', 'kval':[
            KValue("kcat", "", 0.0)
        ]},
        # Unchanging Enzyme Concs:
        'HK' : {'val':7e-3, 'unit':'uM','moltype':'enz', 'kval':[
            KValue("kcat", "", 4e3)
        ]},
        'PEPWELD' : {'val':4.5e-3, 'unit':'uM','moltype':'enz', 'kval':[
            KValue("kcat", "", 1e3)
        ]},
        'PK' : {'val':7.0e-2, 'unit':'uM','moltype':'enz', 'kval':[
            KValue("kcat", "", 1.7e3)
        ]},
}
mol

{'Gluc': {'val': 5000.0,
  'unit': 'uM',
  'moltype': 'met',
  'kval': [KValue(ktype='sat', ktarget='HK', kval=500.0)]},
 'F6P': {'val': 0.0,
  'unit': 'uM',
  'moltype': 'met',
  'kval': [KValue(ktype='sat', ktarget='PFKa', kval=1.0),
   KValue(ktype='sat', ktarget='PFKi', kval=10000000.0),
   KValue(ktype='alloI', ktarget='HK', kval=20.0)]},
 'F16BP': {'val': 0.0,
  'unit': 'uM',
  'moltype': 'met',
  'kval': [KValue(ktype='sat', ktarget='PEPWELD', kval=5000.0),
   KValue(ktype='alloA', ktarget='PK', kval=400.0)]},
 'PEP': {'val': 0.0,
  'unit': 'uM',
  'moltype': 'met',
  'kval': [KValue(ktype='sat', ktarget='PK', kval=35.0),
   KValue(ktype='sat', ktarget='PFKb', kval=0.05)]},
 'ADP': {'val': 560.0,
  'unit': 'uM',
  'moltype': 'met',
  'kval': [KValue(ktype='sat', ktarget='PK', kval=50.0),
   KValue(ktype='sat', ktarget='PFKb', kval=550.0)]},
 'ATP': {'val': 9600.0,
  'unit': 'uM',
  'moltype': 'met',
  'kval': [KValue(ktype='sat', ktarget='PFKa', kval=60.0),
   KValue(ktype='sat'

In [17]:
tfs = []
gain = []

for m in mol.keys():
    for kv in mol[m]['kval']:
        if kv.ktype == 'sat':
            tfs.append(saturation(mol[m]['val'], kv.kval))
        elif kv.ktype == 'alloI':
            tfs.append(alloInhib(mol[m]['val'], kv.kval))
        elif kv.ktype == 'alloA':
            tfs.append(alloAct(mol[m]['val'], kv.kval))
        elif kv.ktype == 'kcat':
            gain.append(kv.kval)
        else:
            if kv == None:
                pass
            else:
                print("uh oh, something went wrong")    


        if kv.ktype != 'kcat':
            print(f"mol: {m} ktype: {kv.ktype} target: {kv.ktarget} val: {tfs[-1]}")
        else:
            print(f"enz: {m} kcat: {kv.kval}")

tfs,gain

mol: Gluc ktype: sat target: HK val: 0.9090909090909091
mol: F6P ktype: sat target: PFKa val: 0.0
mol: F6P ktype: sat target: PFKi val: 0.0
mol: F6P ktype: alloI target: HK val: 1.0
mol: F16BP ktype: sat target: PEPWELD val: 0.0
mol: F16BP ktype: alloA target: PK val: 1.0
mol: PEP ktype: sat target: PK val: 0.0
mol: PEP ktype: sat target: PFKb val: 0.0
mol: ADP ktype: sat target: PK val: 0.9180327868852459
mol: ADP ktype: sat target: PFKb val: 0.5045045045045045
mol: ATP ktype: sat target: PFKa val: 0.9937888198757764
mol: ATP ktype: sat target: PFKi val: 0.9937888198757764
mol: ATP ktype: sat target: HK val: 0.3902439024390244
mol: ATP ktype: alloI target: PK val: 0.5555555555555556
enz: PFKa kcat: 100.0
enz: PFKi kcat: 100.0
enz: PFKb kcat: 0.0
enz: HK kcat: 4000.0
enz: PEPWELD kcat: 1000.0
enz: PK kcat: 1700.0


([0.9090909090909091,
  0.0,
  0.0,
  1.0,
  0.0,
  1.0,
  0.0,
  0.0,
  0.9180327868852459,
  0.5045045045045045,
  0.9937888198757764,
  0.9937888198757764,
  0.3902439024390244,
  0.5555555555555556],
 [100.0, 100.0, 0.0, 4000.0, 1000.0, 1700.0])

In [27]:
relatf = []

for m in mol.keys():
    for kv in mol[m]['kval']:
        if kv.ktype == 'sat':
            # jerryrig to prevent 0s in denom. This is just a metric and will only be used for debugging 
            if mol[m]['val'] == 0:
                mol[m]['val'] += 1e-16


            cv = np.exp( (np.log(mol[kv.ktarget]['val']) - np.log( (1 + kv.kval/mol[m]['val'] )) )   ) / mol[kv.ktarget]['val']
            relatf.append(cv)
            #print(cv)
        
        
        elif kv.ktype == 'alloI':
            cv = np.exp( (np.log(mol[kv.ktarget]['val']) - np.log( (1 + mol[m]['val']/kv.kval )) )   ) / mol[kv.ktarget]['val']
            relatf.append(cv)
        elif kv.ktype == 'alloA':
            cv = np.exp( (np.log(mol[kv.ktarget]['val']) + np.log( (1 + mol[m]['val']/kv.kval )) )   ) / mol[kv.ktarget]['val']
            relatf.append(cv)
        elif kv.ktype == 'kcat':
            gain.append(kv.kval)
        else:
            if kv == None:
                pass
            else:
                print("uh oh, something went wrong")    


        if kv.ktype != 'kcat':
            print(f"mol: {m} ktype: {kv.ktype} target: {kv.ktarget} val: {relatf[-1]}")
        else:
            print(f"enz: {m} kcat: {kv.kval}")


mol: Gluc ktype: sat target: HK val: 0.9090909090909095
mol: F6P ktype: sat target: PFKa val: 9.999999999999967e-17
mol: F6P ktype: sat target: PFKi val: 9.999999999999997e-24
mol: F6P ktype: alloI target: HK val: 1.0000000000000004
mol: F16BP ktype: sat target: PEPWELD val: 2.000000000000004e-20
mol: F16BP ktype: alloA target: PK val: 1.0
mol: PEP ktype: sat target: PK val: 2.857142857142853e-18
mol: PEP ktype: sat target: PFKb val: 1.9999999999999978e-15
mol: ADP ktype: sat target: PK val: 0.9180327868852457
mol: ADP ktype: sat target: PFKb val: 0.5045045045045046
mol: ATP ktype: sat target: PFKa val: 0.9937888198757762
mol: ATP ktype: sat target: PFKi val: 0.9937888198757762
mol: ATP ktype: sat target: HK val: 0.3902439024390246
mol: ATP ktype: alloI target: PK val: 0.5555555555555556
enz: PFKa kcat: 100.0
enz: PFKi kcat: 100.0
enz: PFKb kcat: 0.0
enz: HK kcat: 4000.0
enz: PEPWELD kcat: 1000.0
enz: PK kcat: 1700.0


In [26]:



class Molecule:
    """
    Molecule Data Class structure

    Attributes:
    -----------
        name : `str`, default = ""
            The name of the molecule
        val : `float`, default = 0.0
            The quantity of the molecule
        unit : `str`, default = "count"
            The unit for the quantity of the molecule
        molType: `str`, default = "met"
            The type of molecule.  Currently accepted values are "met" and "enz"
        kval : `dict`, default = {}
            The kvalues associated with the molecule. 
            If the molecule is an enzyme "enz": kvalues indicate kcat and should be {"kval": kval}
            If the Molecule is a metabolite "met", kvalues indicate either KM or Kreg
            

    Notes:
    ------
    Potential Future attributes:
    pos:
    container:
    """
    def __init__(self, name:str = "", val:float = 0.0, unit:str = "count", moltype:str = "met"):
        self.name = name
        self.val = val
        self.unit = unit
        self.moltype = moltype
        self.kval = [[], []]

    def getName(self):
        return self.name

    def addEnzKval(self, enzKval):
        self.kval[1].append(enzKval)

    def __print__(self):
        print(f"name: {self.name}")
        print(f"val: {self.val}")
        print(f"unit: {self.unit}")
        print(f"moltype: {self.moltype}")
        print(f"kval: {self.kval}")

# Breaking this down into molecules, stochiometry, and reactions
Molecules = np.array([Molecule(key, DICT_T0_CONC[key][0], 'uM', DICT_T0_CONC[key][1]) for key in DICT_T0_CONC.keys()])
print(Molecules)
print([Molecules[i].__print__() for i in range(len(Molecules))])
print(Molecules[0].name)
print(Molecules[0].val)
m = Molecules

name: Gluc
val: 5000
unit: uM
moltype: met
kval: [[], []]
name: F6P
val: 0
unit: uM
moltype: met
kval: [[], []]
name: F16BP
val: 0
unit: uM
moltype: met
kval: [[], []]
name: PEP
val: 0
unit: uM
moltype: met
kval: [[], []]
name: ADP
val: 560
unit: uM
moltype: met
kval: [[], []]
name: ATP
val: 9600
unit: uM
moltype: met
kval: [[], []]
name: PYR
val: 0
unit: uM
moltype: met
kval: [[], []]
name: PFKa
val: 0.001
unit: uM
moltype: enz
kval: [[], []]
name: PFKi
val: 0.001
unit: uM
moltype: enz
kval: [[], []]
name: PFKb
val: 0.005
unit: uM
moltype: enz
kval: [[], []]
name: HK
val: 0.007
unit: uM
moltype: enz
kval: [[], []]
name: PEPWELD
val: 0.0045
unit: uM
moltype: enz
kval: [[], []]
name: PK
val: 0.07
unit: uM
moltype: enz
kval: [[], []]
[None, None, None, None, None, None, None, None, None, None, None, None, None]
Gluc
5000


In [27]:
# horribly inefficient -- but it works

for mol in range(len(m)):
    #print(enz, mol)
    if m[mol].name in DICT_KCAT.keys():
        #print(m[mol].name, mol, DICT_KCAT[ m[mol].getName() ])
        #print(m[mol].kval)
        m[mol].kval[1] = [DICT_KCAT[ m[mol].getName() ]]
        #print(m[mol].kval)

    if m[mol].name in DICT_ENZ_SUBSTRATE.keys():
        for effector in DICT_ENZ_SUBSTRATE[m[mol].getName()].keys():
            if effector == 'prod':
                pass
            else:
                for eff in DICT_ENZ_SUBSTRATE[m[mol].getName()][effector]:
                    # Go back through and append the correct kvalue to the correct molecule
                    for omol in range(len(m)):
                        if m[omol].name == eff[0]:
                            if eff[1] == 'sat':
                                m[omol].kval[0].insert(0, (m[mol].getName(), eff[0], eff[1], DICT_KM[f"{m[mol].getName()}_{eff[0]}"])   )
                            elif eff[1] == 'alloI':
                                m[omol].kval[0].append(( m[mol].getName(), eff[0], eff[1], DICT_K_REGULATORY[f"Ki_{m[mol].getName()}_{eff[0]}"])  )
                            elif eff[1] == 'alloA':
                                m[omol].kval[0].append(( m[mol].getName(), eff[0], eff[1], DICT_K_REGULATORY[f"Ka_{m[mol].getName()}_{eff[0]}"])  )
                            

printBlockMessage('DOONE')
print([m[i].__print__() for i in range(len(m))])

############################################
DOONE
############################################
name: Gluc
val: 5000
unit: uM
moltype: met
kval: [[('HK', 'Gluc', 'sat', 500.0)], []]
name: F6P
val: 0
unit: uM
moltype: met
kval: [[('PFKi', 'F6P', 'sat', 10000000.0), ('PFKa', 'F6P', 'sat', 1.0)], []]
name: F16BP
val: 0
unit: uM
moltype: met
kval: [[('PEPWELD', 'F16BP', 'sat', 5000.0)], []]
name: PEP
val: 0
unit: uM
moltype: met
kval: [[('PK', 'PEP', 'sat', 35.0), ('PFKb', 'PEP', 'sat', 0.05)], []]
name: ADP
val: 560
unit: uM
moltype: met
kval: [[('PK', 'ADP', 'sat', 50.0), ('PFKb', 'ADP', 'sat', 550.0)], []]
name: ATP
val: 9600
unit: uM
moltype: met
kval: [[('HK', 'ATP', 'sat', 15000.0), ('PFKi', 'ATP', 'sat', 60), ('PFKa', 'ATP', 'sat', 60)], []]
name: PYR
val: 0
unit: uM
moltype: met
kval: [[], []]
name: PFKa
val: 0.001
unit: uM
moltype: enz
kval: [[], [100.0]]
name: PFKi
val: 0.001
unit: uM
moltype: enz
kval: [[], [100.0]]
name: PFKb
val: 0.005
unit: uM
moltype: enz
kval: [[], []]
name

In [8]:

def TF(enz:Molecule, targets:list):
    # Find the relevant transfer functions
    tfs = [(targets[i], targets[i].kval["met"][j], 0) for i in range(len(targets)) for j in range(len(targets[i].kval["met"])) if targets[i].kval["met"][i]['ktarget'] == enz.name]

    # for each of those:
    for tf in range(len(tfs)):
        if tfs[tf][1]['ktype'] == 'sat':
            tfs[tf][2] = saturation(tfs[tf][0].val, tfs[tf][1]['kval'])
    
    return tfs





In [ ]:
class EnzymeTransferFunction:
    def __init__(self, enzyme:Molecule, targets:list):
        self.vmax = enzyme.val * enzyme.kval[1]
        self.logEnz = np.log(enzyme.val)
        self.saturation = self.getSaturation()
        self.allostery = self.getAllostery()

    def getChildTransferFunctions(self):
        # for each substrate in the substrate list find the values which have the current enzyme as a target
        # Return these as a list
        # Then for each in the stored list, calculate the log Sat factor
        
        pass

    def getAllostery(self):
        # for each substrate in the substrate list find the values which have the current enzyme as a target
        # Return these as a list
        # Then for each in the stored list, calculate the log Sat factor
        pass



In [3]:
def hexokinase(self):
        """ Gluc + ATP --> F6P + ADP; Catalyzed by HK; Allosterically inhibited by Pyruvate and F6P"""
        vmax = self.dictKcat['HK'] * self.molecules['HK'] 
        sat = saturation(self.molecules['Gluc'], self.dictKM['HK_Gluc']) * saturation(self.molecules['ATP'], self.dictKM['HK_ATP'])
        allo =  alloInhib(self.molecules['F6P'], self.dictKreg['Ki_F6P_HK'])
        return vmax * sat * allo

r = ['HK', 'Gluc', 'ATP', 'F6P', 'ADP']
s = [1,-1,-1,0,0] --> [1,0,0,1,1]

### So it gets kinda messy: (And this doesn't even include the ATP/ADP)
['HK', 'Gluc', 'F6P', 'HK*Gluc', HK*F6P(c), HK*F6P(i), HK*Gluc*F6P(i), HK*F6P(c)*F6P(i)]
HK + Gluc <--> HK*Gluc
[-1,-1,0,1,0,0,0,0]
[1,1,0,-1,0,0,0,0]

HK + F6P <--> HK*F6P(i)
[-1,-1,0,0,0,1,0,0]
[1,1,0,0,0,-1,0,0]

HK*Gluc + F6P <--> HK*Gluc*F6P(i)
[0,-1,0,-1,0,0,1,0]
[0,1,0,1,0,0,-1,0]

HK*Gluc --> HK*F6P(c)
[0,0,0,-1,1,0,0,0]

HK*Gluc*F6P(i) --> HK*F6P(c)*F6P(i)
[0,0,0,0,0,0,-1,1]
HK*F6P(c) --> HK + F6P
[1,0,1,0,-1,0,0,0]
HK*F6P(c)*F6P(i) --> HK*F6P(i) + F6P
[0,0,1,0,0,1,0,-1]
HK*F6P(c)*F6P(i) --> HK*F6P(c) + F6P
[0,0,1,0,1,0,0,-1]

In [15]:
#['HK', 'Gluc', 'F6P', 'HK*Gluc', HK*F6P(c), HK*F6P(i), HK*Gluc*F6P(i), HK*F6P(c)*F6P(i)]
glyc = [
    #HK + Gluc <--> HK*Gluc
    [-1,-1,0,1,0,0,0,0],
    [1,1,0,-1,0,0,0,0],
    #HK + F6P <--> HK*F6P(i)
    [-1,-1,0,0,0,1,0,0],
    [1,1,0,0,0,-1,0,0],
    #HK*Gluc + F6P <--> HK*Gluc*F6P(i)
    [0,-1,0,-1,0,0,1,0],
    [0,1,0,1,0,0,-1,0],
    #HK*Gluc --> HK*F6P(c)
    [0,0,0,-1,1,0,0,0],
    #HK*Gluc*F6P(i) --> HK*F6P(c)*F6P(i)
    [0,0,0,0,0,0,-1,1],
    #HK*F6P(c) --> HK + F6P
    [1,0,1,0,-1,0,0,0],
    #HK*F6P(c)*F6P(i) --> HK*F6P(i) + F6P
    [0,0,1,0,0,1,0,-1],
    #HK*F6P(c)*F6P(i) --> HK*F6P(c) + F6P
    [0,0,1,0,1,0,0,-1],
]
glyc

[[-1, -1, 0, 1, 0, 0, 0, 0],
 [1, 1, 0, -1, 0, 0, 0, 0],
 [-1, -1, 0, 0, 0, 1, 0, 0],
 [1, 1, 0, 0, 0, -1, 0, 0],
 [0, -1, 0, -1, 0, 0, 1, 0],
 [0, 1, 0, 1, 0, 0, -1, 0],
 [0, 0, 0, -1, 1, 0, 0, 0],
 [0, 0, 0, 0, 0, 0, -1, 1],
 [1, 0, 1, 0, -1, 0, 0, 0],
 [0, 0, 1, 0, 0, 1, 0, -1],
 [0, 0, 1, 0, 1, 0, 0, -1]]

glycsym = [
    [-a,-a,0,a,0,0,0,0],
    [-c,-c,0,0,0,c,0,0],
    [d,d,0,0,0,-d,0,0], 
    [0,-e,0,-e,0,0,e,0],
    [0,f,0,f,0,0,-f,0], 
    [0,0,0,-g,g,0,0,0], 
    [0,0,0,0,0,0,-h,h], 
    [i,0,i,0,-i,0,0,0], 
    [0,0,j,0,0,j,0,-j], 
    [0,0,k,0,k,0,0,-k], 
]

In [ ]:
#['HK', 'Gluc', 'F6P', 'HK*Gluc', HK*F6P(c), HK*F6P(i), HK*Gluc*F6P(i), HK*F6P(c)*F6P(i)]
glycsym = [
    [-a,-a,0,a,0,0,0,0],#HK + Gluc --> HK*Gluc
    [b,b,0,-b,0,0,0,0], #HK + Gluc <-- HK*Gluc
    [-c,-c,0,0,0,c,0,0],#HK + F6P --> HK*F6P(i)
    [d,d,0,0,0,-d,0,0], #HK + F6P <-- HK*F6P(i)
    [0,-e,0,-e,0,0,e,0],#HK*Gluc + F6P --> HK*Gluc*F6P(i)
    [0,f,0,f,0,0,-f,0], #HK*Gluc + F6P <-- HK*Gluc*F6P(i)
    [0,0,0,-g,g,0,0,0], #HK*Gluc --> HK*F6P(c)
    [0,0,0,0,0,0,-h,h], #HK*Gluc*F6P(i) --> HK*F6P(c)*F6P(i)
    [i,0,i,0,-i,0,0,0], #HK*F6P(c) --> HK + F6P
    [0,0,j,0,0,j,0,-j], #HK*F6P(c)*F6P(i) --> HK*F6P(i) + F6P
    [0,0,k,0,k,0,0,-k], #HK*F6P(c)*F6P(i) --> HK*F6P(c) + F6P
]
glycsym

In [12]:
class EnzymeReaction:
    """
    Reaction Data Class structure (Enzyme transfer Function)

    Attributes:
    -----------
        name : `str`, default = ""
            The name of the reaction
        subs : `list(str)`, default = ['']
            List of molecule names on the LHS of the reaction 
        prod : `list(str)`, default = ['']
            List of molecule names on the RHS of the reaction
        qSubs : `list(int)`, default = [1]
            The quantity of each substrate (stochiometry) consumed in 1 reaction
        qProd : `list(int)`, default = [1]
            The quantity of each product (stochiometry) produced in 1 reaction

    Notes:
    ------
    If a molecule is both a `subs` and a `prod` then it is considered a catalyst

    """
    name: str = ""
    subs: dict = [""]
    prod: list = [""]
    qSubs: list = [1]
    qProd: list = [1]
    
    

In [16]:
class System:
    """
    System Class

    Attributes:
    -----------
        ss : `list(Molecule)` 
            The list of molecules comprising the system state space(ss).
        rxn :  `list(Reaction)`
            The list of reactions between states

    Notes:
    ------

    """
    def __init__(self, ss = [Molecule()], rxn = [Reaction()]):
        self.ss = ss
        self.rxn = rxn    



5000

In [29]:
t = {
    "a":{'1':1, '2':2, '3':3},
    "b":{'1':1, '2':2, '3':3},
    "c":{'1':1, '2':2, '3':3},
}
t

{'a': {'1': 1, '2': 2, '3': 3},
 'b': {'1': 1, '2': 2, '3': 3},
 'c': {'1': 1, '2': 2, '3': 3}}

In [30]:
t['a']['1'] = 1234
t

{'a': {'1': 1234, '2': 2, '3': 3},
 'b': {'1': 1, '2': 2, '3': 3},
 'c': {'1': 1, '2': 2, '3': 3}}

In [13]:
conc = [10**(i/4) for i in range(-28, 20)]
#X, Y, Z = conc, conc, conc
# dict_K= {
# 'HK_Gluc' : 500.0,
# 'HK_ATP' : 15000.0,
# 'Ki_F6P_HK' : 20.0,}

In [15]:
def hexokinase(Gluc, ATP, F6P, Gluc_KM, ATP_KM, F6P_Ki):
        """ Gluc + ATP --> F6P + ADP; Catalyzed by HK; Allosterically inhibited by Pyruvate and F6P"""
        sat = saturation(Gluc, Gluc_KM) * saturation(ATP, ATP_KM)
        allo = alloInhib(F6P, F6P_Ki)
        return sat * allo

def HK_sat_Gluc(Gluc, Gluc_KM=500.0):
    return saturation(Gluc, Gluc_KM)
def HK_sat_ATP(ATP, ATP_KM= 15000.0):
    return saturation(ATP, ATP_KM)
def HK_alloI_F6P(F6P, F6P_Ki=20.0):
    return alloInhib(F6P, F6P_Ki)


In [16]:
X, Y, Z = [HK_sat_Gluc(i) for i in conc], [HK_sat_ATP(i) for i in conc], [HK_alloI_F6P(i) for i in conc]

In [55]:

def pplot_ioEnz(
    #enzName,
    #subsName,
    start = -9,
    stop = 5,
    stepsPerLog10 = 10
    ):
    """# I like the turbo color scale (continuous)"""
    # Set up the scale
    conc = [10**(i/stepsPerLog10) for i in range(start*stepsPerLog10,stop*stepsPerLog10)]

    X, Y, Z = conc, conc, [[HK_sat_Gluc(i)*HK_sat_ATP(j)*100 for j in conc] for i in conc]
    #print(Z)
    # # Basically I need to pass in an enzyme, then 
    # if enzName == "HK":

    fig = go.Figure(
        data = [go.Surface(x = X, y = Y, z = Z, color= Z, colorscale="turbo")],
    )
    # fig.update_traces(contours_z=dict(show=True, usecolormap=True,
    #                               highlightcolor="limegreen", project_z=True))

    # fig.update_xaxes(type = 'log')
    # fig.update_yaxes(type = 'log')                              

    return fig
    

In [57]:

# fig = pplot_ioEnz()
# fig.show()

In [60]:
pplot_ioEnz().show()

In [1]:
import numpy as np
import warnings
from random import random, randrange, randint
from dataclasses import dataclass

from util import printTimestamp, printBlockMessage
from units import cnt2mol, mol2cnt
from modelEq import saturation, alloAct, alloInhib

EXCLUDE_FROM_PLOT = ['HK', 'PEPMAKER', 'PK']
ONE_COUNT_IN_MICROMOLAR = 1.66e-18

DICT_TIME = {
    'simDurationSeconds':5000, #172800, #48 hrs if 1s
    'simStepsPerSecond': 1,
    }
# Format: moleculename: (concentration uM, type) 
# Type can be 'met' for metabolite or 'enz' for enzyme
DICT_T0_CONC = {
            # Changeable met concs
            'Gluc' : (5000, 'met'),
            'F6P' :  (0, 'met'),            # Goal: 8.8mM - https://www.nature.com/articles/nchembio.186.pdf,
            'F16BP' :(0, 'met'),            # Goal: 15.0mM - https://www.nature.com/articles/nchembio.186.pdf
            'PEP' :  (0, 'met'),            # Goal: 0.18mM - https://www.nature.com/articles/nchembio.186.pdf
            'ADP' :  (560, 'met'),          # Goal: 0.56mM - https://www.nature.com/articles/nchembio.186.pdf
            'ATP' :  (9600, 'met'),
            'PYR' :  (0, 'met'),
            # Changeable enz concs
            'PFKa' : (1e-3, 'enz'),
            'PFKi' : (1e-3, 'enz'),
            'PFKb' : (5e-3, 'enz'),
            # Unchanging Enzyme Concs:
            'HK' :   (7e-3, 'enz'),
            'PEPMAKER' : (4.5e-3, 'enz'),
            'PK' :   (7.0e-2, 'enz'),
        }
DICT_KCAT = {
    'PFKa':1e2,
    'PFKi':1e2,
    'HK' : 4e3,
    'PK' : 1.7e3,
    'PEPMAKER' : 1e3
    }
DICT_K = {
    'PFKa-->PFKb':1e-7,
    'PFKi-->PFKb':1e-7,
    'PFKb-->PFKa':1e-7,
    'PFKb-->PFKi':1e-7,
    }
DICT_KM = {
    'PFKb_PFKb':5e-7,
    'PFKb_PFKa':1e-2,
    'PFKb_PFKi':1e-2,
    'PFKb_ADP': 550.0,
    'PFKb_PEP': 5e-2,
    'PFKa_F6P': 1.0,
    'PFKa_ATP': 60,
    'PFKi_F6P': 1e7,
    'PFKi_ATP': 60,
    'HK_Gluc' : 500.0,
    'HK_ATP' : 15000.0,
    'PEPMAKER_F16BP' : 5000.0,
    'PK_PEP' : 35.0,
    'PK_ADP' : 50.0,
    }

# Placeholder: currently not utilized
DICT_K_REGULATORY = {
    # Format: Ka/Ki_Molecule_Target
    # Ki
    'Placeholder' : 0.0,
}

DICT_ENZ_SUBSTRATE = {
    'HK' : {'subs':[('Gluc','sat'), ('ATP','sat')], 'prod':[('F6P','sat'), ('ADP','sat')],},
    'PFKa' :  {'subs':[('F6P','sat'), ('ATP','sat')], 'prod':[('F16BP','sat'), ('ADP','sat')]},
    'PFKi' :{'subs':[('F6P','sat'), ('ATP','sat')], 'prod':[('F16BP','sat'), ('ADP','sat')]},
    'PFKb' : {'subs':[('ADP','sat'), ('PEP','sat')], 'prod':[('PFKa','sat'), ('PFKi','sat')]},
    'PEPMAKER' : {'subs':[('F16BP','sat')], 'prod':[('PEP','sat')]},
    'PK' : {'subs':[('PEP','sat'), ('ADP','sat')], 'prod':[('PYR','sat'), ('ATP','sat')],},    
}

# Breaking this down into molecules, stochiometry, and reactions
Molecules = np.empty(shape = len(DICT_T0_CONC.keys()))

class Glycolysis:
    """
    TODO:
    -----
    Conserved quantities checks
    
    Notes:
    ------
     --> current task --> Current model does not have Glucose saturation in the PFK, just assumes it is always at saturation.
        
    """
    def __init__(self, dictTime, dictConc, dictKcat, dictK, dictKM, dictKReg, perturb:bool = True, verbose:bool = True, silent:bool = False, debug:bool = True):
        # Time parameters
        self.time_simDurationSeconds = dictTime['simDurationSeconds']
        self.time_simStepsPerSecond = dictTime['simStepsPerSecond']
        self.time_totalSteps = self.time_simDurationSeconds * self.time_simStepsPerSecond
        self.time_stepResolution = 1 / self.time_simStepsPerSecond
        self.percComplete = 0

        # Adding in reaction params
        self.dictKcat = dictKcat
        self.dictK = dictK
        self.dictKM = dictKM
        self.dictKreg = dictKReg

        # Init Enzymes, metabolites, etc.
        self.concLegend = [key for key in dictConc.keys()]
        self.enzymeLegend = [key for key in dictConc.keys() if dictConc[key][1] == 'enz']
        # Init Containers for simulation values
        self.time = np.linspace(0, self.time_totalSteps, self.time_totalSteps)
        self.dictCountArrays= {i:np.ones([self.time_totalSteps]) for i in self.concLegend} 
        self.zerosCheck = {i:True for i in self.concLegend} 
        self.molecules = {}  

        self.enzymeMetaboliteLegend = [""]

        # Mass Conservation 
        self.dictRawStepTurnover = {i:np.zeros([self.time_totalSteps]) for i in self.concLegend}
        self.dictAdjustedStepTurnover = {i:np.zeros([self.time_totalSteps]) for i in self.concLegend}  
        
        # Activity Containers (debuging/analysis)
        self.dictEnzymePercentMaxActivty = {i:np.zeros([self.time_totalSteps]) for i in self.enzymeLegend} 

        # QSSA
        self.QSSAFlag = {f"{i}_{j[0]}":False for i in DICT_ENZ_SUBSTRATE.keys() for j in DICT_ENZ_SUBSTRATE[i]['subs']}
        self.QSSAThreshold = 0.01
        self.dictQSSACheck = {f"{i}_{j[0]}":np.zeros([self.time_totalSteps]) for i in DICT_ENZ_SUBSTRATE.keys() for j in DICT_ENZ_SUBSTRATE[i]['subs']}  

        # Init t0 Counts
        for key in self.concLegend:
            # The container for all molecule counts
            self.dictCountArrays[key][0] = dictConc[key][0]  
            # The container for current molecule counts
            self.molecules[key] = dictConc[key][0]

        self.debug = debug
        self.verbose = verbose
        self.perturb = perturb
        self.silent = silent

        self.passPYRConsumption = 0
        self.passATPConsumption = 0
        self.passPEPConsumption = 0

    # Reaction Equations
    # Gluc --> F6P
    def hexokinase(self):
        """ Gluc + ATP --> F6P + ADP; Catalyzed by HK; """
        vmax = self.dictKcat['HK'] * self.molecules['HK'] 
        sat = saturation(self.molecules['Gluc'], self.dictKM['HK_Gluc']) * saturation(self.molecules['ATP'], self.dictKM['HK_ATP'])
        allo = 1
        return vmax * sat * allo

    # PFKi <--> PFKb <--> PFKa
    # TODO: documentation
    def pfkActiveToBase(self):
        return  self.molecules['PFKa'] / self.dictKM['PFKb_PFKa'] * self.dictK['PFKa-->PFKb'] 
    def pfkInactiveToBase(self):
        return  self.molecules['PFKi'] / self.dictKM['PFKb_PFKi'] * self.dictK['PFKi-->PFKb'] 
    def pfkBaseToActive(self):
        return  self.molecules['PFKb'] / self.dictKM['PFKb_PFKb'] * self.dictK['PFKb-->PFKa'] * saturation(self.molecules['ADP'],self.dictKM['PFKb_ADP'])
    def pfkBaseToInactive(self):
        return  self.molecules['PFKb'] / self.dictKM['PFKb_PFKb'] * self.dictK['PFKb-->PFKi'] * saturation(self.molecules['PEP'],self.dictKM['PFKb_PEP'])
    
    # F6P --> F16BP
    def pfk_active(self):
        """ PFKa Catalysis (F6P --> F16BP) Michaelis Menten 1 substrate irreversible"""
        vmax = self.dictKcat['PFKa'] * self.molecules['PFKa'] 
        sat = saturation(self.molecules['F6P'], self.dictKM['PFKa_F6P']) * saturation(self.molecules['ATP'], self.dictKM['PFKa_ATP'])
        allo = 1
        return vmax * sat * allo
    def pfk_inactive(self):
        """ PFKi Catalysis (F6P --> F16BP) Michaelis Menten 1 substrate irreversible"""
        vmax = self.dictKcat['PFKi'] * self.molecules['PFKi'] 
        sat = saturation(self.molecules['F6P'], self.dictKM['PFKi_F6P']) * saturation(self.molecules['ATP'], self.dictKM['PFKi_ATP'])
        allo = 1
        return vmax * sat * allo

    # F16BP --> PEP
    def pepmaker(self):
        vmax = self.dictKcat['PEPMAKER'] * self.molecules['PEPMAKER']
        sat = saturation(self.molecules['F16BP'], self.dictKM['PEPMAKER_F16BP']) 
        allo = 1
        return vmax * sat * allo

    # PEP --> PYR
    def pyruvateKinase(self):
        vmax = self.dictKcat['PK'] * self.molecules['PK']
        sat = saturation(self.molecules['PEP'], self.dictKM['PK_PEP']) * saturation(self.molecules['ADP'], self.dictKM['PK_ADP'])
        allo = 1
        return vmax * sat * allo

    # Passive Consumption:
    # TODO: Make user tuneable/perturbation response
    def passiveATPConsumption(self):
        return self.passATPConsumption * self.molecules['ATP']
    def passivePYRConsumption(self):
        return self.passPYRConsumption * self.molecules['PYR']
    def passivePEPConsumption(self):
        return self.passPEPConsumption * self.molecules['PEP']   

    # Concentration Change equations
    # Delta intermediate carbons
    def dF6P_dt(self):
        influx = self.hexokinase()
        efflux = self.pfk_active() + self.pfk_inactive()
        return influx - efflux
    def dF16BP_dt(self):
        influx = self.pfk_active() + self.pfk_inactive()
        efflux = self.pepmaker()
        return influx - efflux
    def dPEP_dt(self):
        influx = self.pfkInactiveToBase() + self.pepmaker()
        efflux = self.pfkBaseToInactive() + self.passivePEPConsumption()
        return influx - efflux
    
    # Delta secondary metabolites
    def dATP_dt(self):
        influx = self.pyruvateKinase()
        efflux = self.hexokinase() + self.pfk_active() + self.pfk_inactive() + self.passiveATPConsumption()
        return influx - efflux 
    def dADP_dt(self):
        influx = self.pfkActiveToBase() + self.hexokinase() + self.pfk_active() + self.pfk_inactive() + self.passiveATPConsumption()
        efflux = self.pfkBaseToActive() + self.pyruvateKinase()
        return influx - efflux
    
    # delta PFK states 
    def dPFKa_dt(self):
        influx = self.pfkBaseToActive()
        efflux = self.pfkActiveToBase()
        return influx - efflux
    def dPFKi_dt(self):
        influx = self.pfkBaseToInactive()
        efflux = self.pfkInactiveToBase()
        return influx - efflux
    def dPFKb_dt(self):
        influx = self.pfkActiveToBase() + self.pfkInactiveToBase()
        efflux = self.pfkBaseToActive() + self.pfkBaseToInactive()  
        return influx - efflux

    # delta I/O Carbon values
    def dGluc_dt(self):
        influx = 0
        efflux = self.hexokinase() 
        return influx - efflux
    def dPYR_dt(self):
        influx = self.pyruvateKinase()
        efflux = self.passivePYRConsumption()
        return influx - efflux
    
    # 0 Change
    def dZeroChange_dt(self):
        return 0
    def rate(self):
        return {
            #'Gluc' : self.dZeroChange_dt(), 
            'Gluc' : self.dGluc_dt() * self.time_stepResolution,
            'F6P' : self.dF6P_dt() * self.time_stepResolution, 
            'F16BP' : self.dF16BP_dt() * self.time_stepResolution, 
            'PEP' : self.dPEP_dt() * self.time_stepResolution, 
            'ADP' : self.dADP_dt() * self.time_stepResolution,  
            'ATP' : self.dATP_dt() * self.time_stepResolution,  
            'PFKa' : self.dPFKa_dt() * self.time_stepResolution,
            'PFKi' : self.dPFKi_dt() * self.time_stepResolution,
            'PFKb' : self.dPFKb_dt() * self.time_stepResolution,
            'PYR' : self.dPYR_dt() * self.time_stepResolution,
            # Enzymes with fixed concentrations
            'HK' : self.dZeroChange_dt(),
            'PEPMAKER' : self.dZeroChange_dt(),
            'PK' : self.dZeroChange_dt()
        }

    def debugSetRatesToZero(self, lstMolecules:list, dictRates:dict) -> dict:
        """Set specific molecule turnover rates to zero (for debugging)

        Parameters:
        -----------
            lstMoleclues : `list`
                List of molecule names which should have their rates set to 0. These values must match the keys of dictRates.
            dictRates : `dict` 
                Dictionary containing the step turn over (i.e. rate) and molecule name. format: {moleculeName : numberOfMoleculesToTurnOver} 
        Returns:
        --------
            zeroedRates : `dict`
                The input dictionary with zeroed rates matching the lstMolecules.
        """ 
        zeroedDictRates = {}
        for key in dictRates.keys():
            if key in lstMolecules:
                zeroedDictRates[key] = 0
            else:
                zeroedDictRates[key] = dictRates[key]
        return zeroedDictRates

    def updateMolecules(self, step):
        for key in self.molecules.keys():
            self.molecules[key] = self.dictCountArrays[key][step]

    # TODO: Document and add set of tuning perturbations
    def perturbation(self, step):     
        
        # Change passive consumption rates
        if step % 100 == 0:
            self.passPYRConsumption = randint(1, 5) * 10 ** randrange(-2, -1, 1)
            #self.passATPConsumption = (randint(1,12) - 1/randint(3, 8)) * 10 ** randrange(-6, -5, 1)            
            self.passATPConsumption = (randint(1,12) - 1/randint(3, 8)) * 10 ** randrange(-3, -2, 1)            
            self.passPEPConsumption = randint(1, 3) * 10 ** randrange(-2, -1, 1)   

        # Change glucose concentration
        if step % 500 == 0:
            newGluc = 5*random() * 10 ** randrange(0,6, 1)
            self.dictCountArrays['Gluc'][step] = newGluc
            self.molecules['Gluc'] = newGluc   


    def saveStepVmax(self, step):
        """ Look at each enzyme, get the current step vmax."""
        for key in self.dictEnzymePercentMaxActivty.keys():
            self.dictEnzymePercentMaxActivty[key][step] = self.dictKcat[key] * self.molecules[key]

    def checkAssertions(self,step):
        # Total mass conservation:
        totalPFK = self.dictCountArrays['PFKa'][0] + self.dictCountArrays['PFKi'][0] + self.dictCountArrays['PFKb'][0]
        if abs(self.molecules['PFKa'] + self.molecules['PFKi'] + self.molecules['PFKb'] - totalPFK) > 1e-12:
            if self.debug:
                warnings.warn(f"On Step: {step} PFK mass Not Conserved! \n Correct Total: {totalPFK}  Actual Total: {self.molecules['PFKa'] + self.molecules['PFKi'] + self.molecules['PFKb']}  Difference: {self.molecules['PFKa'] + self.molecules['PFKi'] + self.molecules['PFKb'] - totalPFK}")
            else: 
                #TODO: make assertion for "non-debug state"
                #assert 
                pass
                
            if self.verbose:
                print(f"Previous step values -- PFKb: {self.dictCountArrays['PFKb'][step-1]} PFKa: {self.dictCountArrays['PFKa'][step-1]} PFKi: {self.dictCountArrays['PFKi'][step-1]}")
                print(f"Current step values -- PFKb: {self.dictCountArrays['PFKb'][step]} PFKa: {self.dictCountArrays['PFKa'][step]} PFKi: {self.dictCountArrays['PFKi'][step]}")
                print(f"Difference -- PFKb: {self.dictCountArrays['PFKb'][step] - self.dictCountArrays['PFKb'][step-1]} PFKa: {self.dictCountArrays['PFKa'][step] - self.dictCountArrays['PFKa'][step-1]} PFKi: {self.dictCountArrays['PFKi'][step] - self.dictCountArrays['PFKi'][step-1]}")

        
        totalADPATP = self.dictCountArrays['ATP'][0] + self.dictCountArrays['ADP'][0] + self.dictCountArrays['PFKa'][0]
        if abs(self.molecules['ATP'] + self.molecules['ADP'] + self.molecules['PFKa'] - totalADPATP) > 1e-6:
            if self.debug:
                warnings.warn(f"On Step: {step} ATP-ADP mass Not Conserved! \n Correct Total: {totalADPATP}  Actual Total: {self.molecules['ATP'] + self.molecules['ADP'] + self.molecules['PFKa']}  Difference: {self.molecules['ATP'] + self.molecules['ADP'] + self.molecules['PFKa']- totalADPATP}")
            else: 
                #TODO: make assertion for "non-debug state"
                #assert 
                pass
            
            if self.verbose:
                print(f"Passive ATP Consumption: {self.passATPConsumption} Passive PEP Consumption: {self.passPEPConsumption} Passive PYR Consumption: {self.passPYRConsumption}")

        # Assert no concentration goes subatomic
        for key in self.dictCountArrays.keys():
            #assert (self.dictCountArrays[key][step] > approx1MoleculeInuM), f"On step {step}, {key} has gone into subatomic counts!!"
            if self.dictCountArrays[key][step] < ONE_COUNT_IN_MICROMOLAR and self.dictCountArrays[key][0] > ONE_COUNT_IN_MICROMOLAR:
                warnings.warn(f"On step {step}, {key} has gone into subatomic counts!!") 

        # Quasi-Steady State Validity Check:
        # E / (S + Km) << 1
        for key in self.dictQSSACheck.keys():
            # key is formatted: enzymeName_substrate thus: key.split("_")[0] extracts the enzyme
            enz, subs = key.split("_")[0], key.split("_")[1]

            qssa = self.molecules[enz] / (self.molecules[subs] + self.dictKM[f"{enz}_{subs}"])
            self.dictQSSACheck[key][step] = qssa > self.QSSAThreshold # Note: True indicates a violation of QSSA
            
            # Flag the QSSA violation to the threshold
            if self.dictQSSACheck[key][step] and not self.QSSAFlag[key]:
                warnings.warn(f"On step {step}, {enz} has violated the QSSA for {subs}!!") 
                self.QSSAFlag[key] = True


    def printStatements(self, step, rawRate):
        if step % 1000 == 0:
                self.percComplete = round((step*100 / self.time_totalSteps),1)
                printBlockMessage(f"Step: {step}. Simulation is {self.percComplete}% Complete.")
                print(f"Is Molecule Concentration 0? {self.zerosCheck}")
                print(f"Accumulated ATP-ADP error: {self.molecules['ATP'] + self.molecules['ADP'] + self.molecules['PFKa'] - (self.dictCountArrays['ATP'][0] + self.dictCountArrays['ADP'][0] + self.dictCountArrays['PFKa'][0])}")
                print(f"Molecule Turnover rates: { {key:self.dictRawStepTurnover[key][step] for key in self.dictRawStepTurnover.keys()} }")
                #print(rawRate)

    def run(self):
        if not self.silent:
            printBlockMessage("Begin simulation...", ts =True)
        for step in range(1,self.time_totalSteps):       
            # Calculate raw concentration changes for current step.
            rawRate = self.rate()

            # Debugging: Save the raw turnover rate
            if self.debug:
                for key in rawRate.keys():
                    self.dictRawStepTurnover[key][step] = rawRate[key]
                    
            # Mass Conservation
            self.zerosCheck = { key:self.molecules[key] + rawRate[key] > ONE_COUNT_IN_MICROMOLAR for key in self.dictCountArrays.keys()}
            for key in self.dictCountArrays.keys():
                self.dictAdjustedStepTurnover[key][step] = rawRate[key] * self.zerosCheck[key]
                self.dictCountArrays[key][step] = self.molecules[key] + self.dictAdjustedStepTurnover[key][step]

            # update current counts
            self.updateMolecules(step)
            
            # Check for purturbation:
            if self.perturb:
                self.perturbation(step)

            if self.debug:
                self.checkAssertions(step)
            
            if self.verbose:
                self.printStatements(step, rawRate)

        if not self.silent:
            printBlockMessage("Simulation Complete!", ts =True)
        return self.time, self.dictCountArrays, self.dictEnzymePercentMaxActivty, self.dictQSSACheck

In [25]:
def generateRGBList(n:int) -> list:
    ''' generate n rgb strings and return the list for plotly colors'''
    outputRGBs = [f'rgb({randint(0,255)},{randint(0,255)},{randint(0,255)})' for val in range(n)]
    return outputRGBs

In [2]:
"""

"""
import numpy as np

from copy import deepcopy

from util import printTimestamp, printBlockMessage
from units import cnt2mol

class Titration:
    """ Perform titration on a model.
    """
    def __init__(self, model, inputName: str, outputName: str, inputGridSearchRange = np.logspace(-9, 2, 12), maxSteps = 5000) -> None:
        self.model = deepcopy(model)
        self.inputName = inputName
        self.outputName = outputName
        self.inputGridSearchRange = inputGridSearchRange
        self.maxSteps = maxSteps
        self.titrationResults = {}

    def _findMaxTimeKey(self):
        assert self.titrationResults == True, "Titration results appears to be empty! Did the `run` method get called?" 
        # Gets a tuple from each exp with (expName, maxTimepoint)
        titrationTimes = [(key, self.titrationResults[key]['time'][-1]) for key in self.titrationResults.keys()]
        # return the key from the titration with the largest 'time' value
        return max(titrationTimes, key=lambda tup: tup[1])[0]

    def run(self):
        # This is sloppy, but may work for now.
        # Basically I need to modify the inital condition of the concentration
        printBlockMessage("Beginning Titration experiment...", ts = True)
        for conc in self.inputGridSearchRange:
            print(f"Beginning simulation for {self.inputName} with concentration {conc}")
            # Set up, copy base model
            currModel = deepcopy(self.model)
            # Input the experimental params
            currModel.time_totalSteps = self.maxSteps
            currModel.perturb = False
            currModel.silent = True
            currModel.dictCountArrays[self.inputName][0] = conc
            currModel.molecules[self.inputName] = conc
            # Run sim with updated params
            outT, outC, _, _ = currModel.run()

            # Save sim results
            self.titrationResults[f'{self.inputName}_{conc}'] = {'time':outT, 'conc':{key:outC[key] for key in outC.keys() if key in [self.inputName, self.outputName]}}
            ## REPEAT
        
        printBlockMessage("Titration experiment complete!", ts = True)
        # Return the desired output results.
        return self.titrationResults

In [3]:
sim = Glycolysis(DICT_TIME, DICT_T0_CONC, DICT_KCAT, DICT_K, DICT_KM, DICT_K_REGULATORY)
exp = Titration(sim, 'Gluc', 'ATP')
titrationOutput = exp.run()


############################################
Beginning Titration experiment...
Time: 15:05:54
############################################
Beginning simulation for Gluc with concentration 1e-09
############################################
Step: 1000. Simulation is 20.0% Complete.
############################################
Is Molecule Concentration 0? {'Gluc': False, 'F6P': False, 'F16BP': True, 'PEP': True, 'ADP': True, 'ATP': True, 'PYR': True, 'PFKa': True, 'PFKi': True, 'PFKb': True, 'HK': True, 'PEPMAKER': True, 'PK': True}
Accumulated ATP-ADP error: -5.4569682106375694e-12
Molecule Turnover rates: {'Gluc': -3.7036270208955486e-20, 'F6P': -9.75068310763975e-19, 'F16BP': -3.825036584776478e-13, 'PEP': 9.873800267634974e-09, 'ADP': -3.0943461802450635e-05, 'ATP': 3.093358813225249e-05, 'PYR': 3.093358813225354e-05, 'PFKa': 9.8736701981462e-09, 'PFKi': -9.873417762964392e-09, 'PFKb': -2.5243518181229776e-13, 'HK': 0.0, 'PEPMAKER': 0.0, 'PK': 0.0}
####################################

C:\Users\austi\AppData\Local\Temp/ipykernel_4516/478696114.py:372: UserWarning: On step 1, PFKb has violated the QSSA for PEP!!
  warnings.warn(f"On step {step}, {enz} has violated the QSSA for {subs}!!")


############################################
Step: 3000. Simulation is 60.0% Complete.
############################################
Is Molecule Concentration 0? {'Gluc': False, 'F6P': False, 'F16BP': True, 'PEP': True, 'ADP': True, 'ATP': True, 'PYR': True, 'PFKa': True, 'PFKi': True, 'PFKb': True, 'HK': True, 'PEPMAKER': True, 'PK': True}
Accumulated ATP-ADP error: -4.729372449219227e-11
Molecule Turnover rates: {'Gluc': -3.703655943941567e-20, 'F6P': -9.783519572693204e-19, 'F16BP': -6.317620376340022e-14, 'PEP': 9.624528682438193e-09, 'ADP': -9.17984082020083e-05, 'ATP': 9.178878352873616e-05, 'PYR': 9.178878352873722e-05, 'PFKa': 9.62467327213509e-09, 'PFKi': -9.624465505219042e-09, 'PFKb': -2.0776691604127316e-13, 'HK': 0.0, 'PEPMAKER': 0.0, 'PK': 0.0}
############################################
Step: 4000. Simulation is 80.0% Complete.
############################################
Is Molecule Concentration 0? {'Gluc': False, 'F6P': False, 'F16BP': True, 'PEP': True, 'ADP': True, 

In [8]:
titrationOutput

list(titrationOutput.keys())[0]

'Gluc_1e-09'

In [39]:
titrationOutput.keys()
titrationOutput['Gluc_1e-05']['conc']
#titrationOutput[max([(key, titrationOutput[key]['time'][-1]) for key in titrationOutput.keys()], key=lambda tup: tup[1])[0]]['time']
# Gets the key from the titration with the largest 'time' value
#max([(key, titrationOutput[key]['time'][-1]) for key in titrationOutput.keys()], key=lambda tup: tup[1])[0]


{'Gluc': array([1.00000000e-05, 9.78146342e-06, 9.56770266e-06, ...,
        1.00000000e+00, 1.00000000e+00, 1.00000000e+00]),
 'ATP': array([9.6e+03, 9.6e+03, 9.6e+03, ..., 1.0e+00, 1.0e+00, 1.0e+00])}

In [40]:
import math
import plotly.express as px
import plotly.graph_objects as go
import numpy as np
from heapq import heapify
from random import randint
from plotly.subplots import make_subplots
# Custom
from modelEq import saturation, alloAct, alloInhib
def pplot_titration(
    titrationOutput:dict,
    yAxisScaleMetabolite = 'log'
    ):
    """
    
    Note: all experiemnts must have same step size (but not necessarily same max num steps)
    """
    FORMAT_TITLEFONT = dict(family = 'Arial',size = 16, color = 'rgb(0,0,0)')

    fig = make_subplots(
        rows = 1, cols = 6, 
        specs = [
            [{"colspan":6}, None, None, None, None, None],
 #           [{"colspan":3}, None, None,{"colspan":3}, None, None],
 #           [{"colspan":3}, None, None,{"colspan":3}, None, None],
        ],
        shared_xaxes= True,
        subplot_titles=("Molecule Concentrations",)
    )

     # return the key from the titration with the largest 'time' value
    X = titrationOutput[max([(key, titrationOutput[key]['time'][-1]) for key in titrationOutput.keys()], key=lambda tup: tup[1])[0]]['time']

    # Ensure no "0" values (for the sake of log scale):
    for expCondition in titrationOutput.keys():
        for trackedMol in titrationOutput[expCondition]['conc'].keys():
            if titrationOutput[expCondition]['conc'][trackedMol][0] == 0:
                titrationOutput[expCondition]['conc'][trackedMol][0] = 1e-18

    Y = [titrationOutput]

    # TODO: scale line color based on concentration 
    #metaboliteColors = {key:generateRGBList(1) for key in titrationOutput.keys()}
    

    # [metabolites]
    for exp in titrationOutput.keys():
        for mol in titrationOutput[exp]['conc'].keys():
            fig.add_trace(
                # The line
                go.Scatter(
                    x = X, y = Y[0][exp]['conc'][mol],
                    mode = 'lines', name = f'{exp}_{mol}', text = f'{exp}_{mol}',
                    #line = dict(color = metaboliteColors[key][0]),
                    connectgaps = True,
                ), row = 1, col = 1)
        
            fig.add_trace(go.Scatter(
                x=[( X[0]+X[-1] + np.random.randint(-100,100)) // 2 ], # Add variable name (with a bit of random jitter so they don't overlap)
                y=[Y[0][exp]['conc'][mol][len(X) // 2]],
                mode='text', name = f'{exp}_{mol}', text = f'{exp}_{mol}',
                #marker = dict(color = metaboliteColors[key][0]),
                showlegend = False
            ), row = 1, col = 1)

            # Points at t0 and tn (start and end)
            fig.add_trace(go.Scatter(
                x=[X[0], X[-1]],
                y=[Y[0][exp]['conc'][mol][0], Y[0][exp]['conc'][mol][-1]],
                mode='markers', name = f'{exp}_{mol}', text = f'{exp}_{mol}',
                #marker = dict(color = metaboliteColors[key][0]),
                showlegend = False
            ), row = 1, col = 1)

    fig.update_xaxes(title_text = "steps", titlefont = FORMAT_TITLEFONT,
            showline=True,
            showgrid=True,
            showticklabels=True,
            linecolor='rgb(0, 0, 0)',
            linewidth=2, 
            ticks='outside',
            tickfont=dict(
                family='Arial',
                size=16,
                color='rgb(0, 0, 0)',
            ))

    fig.update_yaxes(title_text = "Concentration (uM)", 
            titlefont = FORMAT_TITLEFONT,
            type = yAxisScaleMetabolite,
            # TODO: Implement dynamic range
            range = [-20, 5],
            showline=True,
            showgrid=True,
            showticklabels=True,
            linecolor='rgb(0, 0, 0)',
            linewidth=2, 
            ticks='outside',
            tickfont=dict(
                family='Arial',
                size=16,
                color='rgb(0, 0, 0)',
            ), row = 1, col = 1)  

    fig.update_layout(
        autosize=True,   
        legend = dict(
            orientation = "h",
        ),
        plot_bgcolor='white'
        )

    if yAxisScaleMetabolite == 'log':
        fig.add_hline(y = 1.66e-18, line_dash = "dot",line_color = "red")
        fig.add_annotation(x = max(X), y = math.log10(0.5e-18), text = "Zero Concentration Threshold", showarrow = False)

    return fig


In [45]:
pplot_titration(titrationOutput)